In [1]:
import torch
torch._dynamo.config.cache_size_limit = 64
torch._dynamo.config.suppress_errors = True
torch.set_float32_matmul_precision('high')

import ChatTTS
from IPython.display import Audio

c:\Users\wuche\anaconda3\envs\chattts\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Load Models

In [2]:
chat = ChatTTS.Chat()
chat.load_models()

# Use force_redownload=True if the weights updated.
# chat.load_models(force_redownload=True)

# If you download the weights manually, set source='locals'.
# chat.load_models(source='local', local_path='YOUR LOCAL PATH')

INFO:ChatTTS.core:Load from cache: C:\Users\wuche/.cache/huggingface\hub/models--2Noise--ChatTTS/snapshots\3b34118f6d25850440b8901cef3e71c6ef8619c8
INFO:ChatTTS.core:use cuda:0
d:\ChatTTS\ChatTTS\core.py:85: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Pleas

## Inference

### Batch infer

In [3]:
texts = ["I prefer cycling to travelling by bus. Cycling is so much more convenient than taking the bus if you are not travelling too far. Actually, it is often faster to go by bike because you don’t get stuck in trafﬁc congestion! Cycling is also better for my health than all other means of transport because it is a form of physical exercise."]*3
        
wavs = chat.infer(texts)

INFO:ChatTTS.core:All initialized.
 NeMo-text-processing :: INFO     :: Creating ClassifyFst grammars.
INFO:NeMo-text-processing:Creating ClassifyFst grammars.


KeyboardInterrupt: 

In [5]:
was=wavs[0]
Audio(was, rate=24_000, autoplay=True)


In [7]:
was=wavs[1]
Audio(was, rate=24_000, autoplay=True)

In [69]:
was=wavs[2]
Audio(was, rate=24_000, autoplay=True)

In [8]:
# 保存音频文件
import numpy as np
from scipy.io.wavfile import write

# 假设wavs[0]是包含音频数据的二维数组
audio_data = np.array(wavs[0])

# 确保音频数据是一维数组
audio_data = audio_data.flatten()

# 确保音频数据在-1.0到1.0之间
audio_data = np.clip(audio_data, -1.0, 1.0)

# 将音频数据转换为int16类型
audio_data = (audio_data * 32767).astype(np.int16)

# 设置采样率为24,000 Hz
rate = 24000

# 将音频数据保存为WAV文件
output_file = "output_audio.wav"
write(output_file, rate, audio_data)
print(f"Audio file saved as {output_file}")

Audio file saved as output_audio.wav


In [36]:
Audio(wavs[2], rate=24_000, autoplay=True)

### Custom params

In [11]:
params_infer_code = {'prompt':'[speed_5]', 'temperature':.3}
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'}



In [ ]:
wav = chat.infer('四川美食可多了，有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片等，每样都让人垂涎三尺。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

In [7]:
Audio(wav[0], rate=24_000, autoplay=True)

搞一个网上嵌入的pt,替换pt就是替换音色.

In [8]:
import torch
import torch.nn as nn

# 加载嵌入向量 (如果是 SlidingWindowFeature 对象)
embedding = torch.load('speaker_embedding.pt', map_location=torch.device('cpu'))

# 检查是否是 SlidingWindowFeature 对象，并提取实际数据
if hasattr(embedding, 'data'):
    embedding = embedding.data

# 对时间维度取平均，得到一个 (512,) 的向量
embedding = embedding.mean(dim=0)  # 对时间维度求平均

# 使用线性变换将 512 维映射到 768 维
linear_layer = nn.Linear(512, 768)
embedding_768 = linear_layer(embedding.unsqueeze(0)).squeeze(0)  # 变换后再去除 batch 维度

# 打印映射后的嵌入形状
print("Embedding shape after linear transformation:", embedding_768.shape)

# 检查嵌入向量是否为 768 维
assert embedding_768.shape[0] == 768, "Embedding dimension mismatch!"

# 继续后续代码逻辑
params_infer_code = {'spk_emb': embedding_768}
wav = chat.infer('I prefer cycling to travelling by bus. Actually, it is often faster to go by bike because you don’t get stuck in trafﬁc congestion!', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)


/var/folders/_2/qv4ggy2904gf544vsztybqc00000gn/T/ipykernel_44046/3240784061.py:5: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  embedding = torch.load('speaker_embedding.pt'

AttributeError: 'memoryview' object has no attribute 'mean'

In [14]:
em=chat.sample_random_speaker()
print(em)

tensor([ 8.5053e-01,  8.6467e+00, -1.4773e+01,  3.2871e+00,  1.7551e+00,
         3.1270e+00,  7.1476e+00, -3.5257e-01, -3.3056e-01, -4.1631e+00,
         5.5662e+00,  4.8906e-01,  6.6527e-01,  1.5715e+00, -8.1949e+00,
         3.4307e+00, -1.8199e+00, -7.0771e+00,  2.7266e+00, -3.6322e+00,
         8.2789e+00,  3.0258e+00,  4.6012e+00,  1.0763e+01, -7.1013e-01,
        -1.9386e-01, -5.9715e+00, -1.5363e+00,  3.8445e-01, -1.4784e+00,
         1.1453e+01, -7.7752e-01, -3.5129e+00, -4.3532e-01, -2.5768e+00,
        -9.1136e+00,  8.3321e-01, -1.9004e+00,  3.5144e+00, -3.6379e+00,
        -2.7616e+00,  3.5859e+00,  1.0585e+01, -6.9825e-01, -9.7083e+00,
        -3.4265e+00,  2.4203e+00, -6.5620e+00, -2.8597e+00, -1.1509e+00,
         1.3305e+00,  4.6145e+00,  6.7323e+00, -9.7926e-01, -5.4345e+00,
         5.2047e+00, -9.2620e-02,  1.7706e+00,  2.6634e+00,  1.9577e+00,
        -3.0218e+00, -3.9571e+00,  2.2631e+00, -3.0826e+00, -2.8007e+00,
         1.5568e+00, -2.5640e+00, -1.3118e+01, -6.2

In [12]:
import torch

params_refine_text = {'prompt':'[break_1][oral_2]'}
# 加载保存的嵌入向量
embedding = torch.load('seed_1518_restored_emb.pt', map_location=torch.device('cpu'))
# embedding = embedding.squeeze()
#print("Loaded embedding shape:", embedding)

# 确认嵌入向量的维度是否正确
assert embedding.shape[0] == 768, "Embedding dimension mismatch!"  # 假设你的目标维度是768
#params_infer_code={'spk_emb':embedding}
params_infer_code = {'spk_emb': embedding, 'temperature':.3, 'top_P':0.7, 'top_K':20}
texts = """I prefer cycling to travelling by bus . Actually, it is often faster to go by bike because you don't get stuck in traffic congestion!"""
wav = chat.infer(texts, \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)
Audio(wav[0], rate=24_000, autoplay=True)

C:\Users\wuche\AppData\Local\Temp\ipykernel_27072\157925357.py:5: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  embedding = torch.load('seed_1518_restored_emb.pt', map_locat

In [22]:
wav = chat.infer('I prefer cycling to travelling by bus. Actually, it is often faster to go by bike because you don’t get stuck in traffic congestion! ', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)
Audio(wav[0], rate=24_000, autoplay=True)

INFO:ChatTTS.core:All initialized.
 18%|█▊        | 377/2048 [00:10<00:44, 37.39it/s]


### fix random speaker

In [8]:
#采样一个说话者
rand_spk = chat.sample_random_speaker()
# print(rand_spk)  # 打印并保存嵌入向量

# 将嵌入向量保存到文件中
with open('saved_speaker_embedding.txt', 'w') as f:
    f.write(','.join(map(str, rand_spk.tolist())))
print(f"Speaker embedding saved as saved_speaker_embedding.txt")


INFO:ChatTTS.core:All initialized.


Speaker embedding saved as saved_speaker_embedding.txt


  8%|▊         | 169/2048 [00:03<00:44, 42.64it/s]


这个是加载官方的随机向量

In [5]:
# 从文件中加载嵌入向量
with open('saved_speaker_embedding_get.txt', 'r') as f:
    saved_spk = list(map(float, f.read().strip().split(',')))
params_infer_code = {'spk_emb' : torch.tensor(saved_spk),'prompt':'[speed_5]', 'temperature':.3 }

这个是加载大尤的声音向量

In [9]:
with open('saved_speaker_embedding_get.txt', 'r') as f:
    saved_spk = list(map(float, f.read().strip().split(',')))
#将加载的嵌入向量转换为tensor
import torch
fixed_spk = torch.tensor(saved_spk)


import torch.nn as nn

class EmbeddingAdapter(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(EmbeddingAdapter, self).__init__()
        self.fc = nn.Linear(input_dim, output_dim)

    def forward(self, x):
        return self.fc(x)

# 初始化适配器层，将256维嵌入向量转换为768维
adapter = EmbeddingAdapter(input_dim=256, output_dim=768)

# 将适配器层应用到嵌入向量
fixed_spk_adapted = adapter(fixed_spk.unsqueeze(0)).squeeze(0)

params_infer_code = {'spk_emb' : fixed_spk_adapted,'prompt':'[speed_5]', 'temperature':.3  }
params_refine_text = {'prompt':'[oral_2]'}
# # print(rand_spk)
# wav = chat.infer('四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃口味温和，甜而不腻，也很受欢迎。', \
#     params_refine_text=params_refine_text, params_infer_code=params_infer_code)
wav = chat.infer("Do you prefer to travel by bike or by bus?", \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)


#wav = chat.infer("Do you prefer to travel by bike or by bus?[uv_break] \
#I prefer cycling to travelling by bus. Cycling is so much more convenient than taking the bus if you are not travelling too far. Actually, it is often faster to go by bike because I won't get stuck in trafﬁc congestion! Cycling is also better for my health than all other means of transport because it is a form of physical exercise.", \
#    params_refine_text=params_refine_text, params_infer_code=params_infer_code)
Audio(wav[0], rate=24_000, autoplay=True)

INFO:ChatTTS.core:All initialized.
  9%|▉         | 182/2048 [00:05<00:53, 35.02it/s]


In [8]:
wav = chat.infer("Do you prefer to travel by bike or by bus?", \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)


#wav = chat.infer("Do you prefer to travel by bike or by bus?[uv_break] \
#I prefer cycling to travelling by bus. Cycling is so much more convenient than taking the bus if you are not travelling too far. Actually, it is often faster to go by bike because I won't get stuck in trafﬁc congestion! Cycling is also better for my health than all other means of transport because it is a form of physical exercise.", \
#    params_refine_text=params_refine_text, params_infer_code=params_infer_code)
Audio(wav[0], rate=24_000, autoplay=True)

INFO:ChatTTS.core:All initialized.
  9%|▉         | 183/2048 [00:04<00:49, 37.99it/s]


In [12]:
#采样一个说话者
rand_spk = chat.sample_random_speaker()
# print(rand_spk)  # 打印并保存嵌入向量

# 将嵌入向量保存到文件中
# with open('saved_speaker_embedding.txt', 'w') as f:
#     f.write(','.join(map(str, rand_spk.tolist())))
# print(f"Speaker embedding saved as saved_speaker_embedding.txt")
# 从文件中加载嵌入向量
with open('saved_speaker_embedding.txt', 'r') as f:
    saved_spk = list(map(float, f.read().strip().split(',')))
params_infer_code = {'spk_emb' : torch.tensor(saved_spk), }
wav = chat.infer('I prefer cycling to travelling by bus. Cycling is so much more convenient than taking the bus if you are not travelling too far.', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)
Audio(wav[0], rate=24_000, autoplay=True)

INFO:ChatTTS.core:All initialized.
 21%|██        | 434/2048 [00:13<00:50, 31.76it/s]


In [13]:
# 保存音频文件
import numpy as np
from scipy.io.wavfile import write

# 假设wavs[0]是包含音频数据的二维数组
audio_data = np.array(wav[0])

# 确保音频数据是一维数组
audio_data = audio_data.flatten()

# 确保音频数据在-1.0到1.0之间
audio_data = np.clip(audio_data, -1.0, 1.0)

# 将音频数据转换为int16类型
audio_data = (audio_data * 32767).astype(np.int16)

# 设置采样率为24,000 Hz
rate = 24000

# 将音频数据保存为WAV文件
output_file = "output_audio.wav"
write(output_file, rate, audio_data)
print(f"Audio file saved as {output_file}")

Audio file saved as output_audio.wav


### Two stage control

In [10]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
chat.infer(text, refine_text_only=True)

INFO:ChatTTS.core:All initialized.
 23%|██▎       | 87/384 [00:00<00:01, 150.60it/s]


['so we found being competitive and collaborative [uv_break] was a huge way of staying [uv_break] motivated towards our goals, [uv_break] so [uv_break] one person to call [uv_break] when you fall off, [uv_break] one person who [uv_break] gets you back [uv_break] on then [uv_break] one person [uv_break] to actually do the activity with.']

In [11]:
text = 'so we found being competitive and collaborative [uv_break] was a huge way of staying [uv_break] motivated towards our goals, [uv_break] so [uv_break] one person to call [uv_break] when you fall off, [uv_break] one person who [uv_break] gets you back [uv_break] on then [uv_break] one person [uv_break] to actually do the activity with.'
wav = chat.infer(text, skip_refine_text=True)

INFO:ChatTTS.core:All initialized.
 49%|████▊     | 995/2048 [00:07<00:07, 141.85it/s]


## LLM Call

In [12]:
from ChatTTS.experimental.llm import llm_api

API_KEY = ''
client = llm_api(api_key=API_KEY,
        base_url="https://api.deepseek.com",
        model="deepseek-chat")

In [13]:
user_question = '四川有哪些好吃的美食呢?'
text = client.call(user_question, prompt_version = 'deepseek')
print(text)
text = client.call(text, prompt_version = 'deepseek_TN')
print(text)

INFO:httpx:HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 200 OK"


四川美食可多了, 有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片、串串香、龙抄手、宜宾燃面、乐山钵钵鸡等, 每样都让人垂涎三尺。


INFO:httpx:HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 200 OK"


四川美食可多了，有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片、串串香、龙抄手、宜宾燃面、乐山钵钵鸡等，每样都让人垂涎三尺。


In [14]:
params_infer_code = {'spk_emb' : rand_spk, 'temperature':.3}

wav = chat.infer(text, params_infer_code=params_infer_code)

INFO:ChatTTS.core:All initialized.
 32%|███▏      | 647/2048 [00:04<00:09, 140.27it/s]
